## Lecture 02  
## Python Performance Tips  
### Feb. 04, 2020  

- https://nyu-cds.github.io/python-performance-tips/

- https://wiki.python.org/moin/PythonSpeed/PerformanceTips

- Python is a dynamic interpreted language (not a compiled language)

- It is not compiled to the native object code and executed on a computer system

- **Types** of variables, function arguments, etc. are not known until the program runs

- Dynamic interpreted languages have great flexibility, but suffer significant performance limitations

- Difficult to optimize


---

- Python is easy to learn, write, read, debug

- A large library of built-in functions and libraries: https://docs.python.org/3/library/functions.html

---


### How to optimize?

- Get the program to give correct results

- Then rerun to see if the correct program is slow

- Profile to find which parts of the program consume most of the time 

- Repeat

### Today's topics: 

- Built-in functions

- Function Call Overhead

- Function Decorator

- Loops, and built-in operators

- Membership operator **in** 


## Timing Python Code

In [1]:
#manually to time:

import time

start_time = time.time()

#factorial 500! = 1 * 2 * 3 * ... * 500
fact = 1
for i in range(500): 
    fact *= i
    
end_time = time.time()

print("run_time: %f" % (end_time - start_time)) #it is in seconds

run_time: 0.000295


In [3]:
# Timing Python Code
# timeit module
# To see how long it takes a program to run once;
# on average over a bunch of runs, e.g. over k=10000 runs;

import timeit

def my_function():
    fact = 1
    for i in range(500): 
        fact *= i


k = 10_000
print("run_time:", timeit.timeit(my_function, number=k) / k)

run_time: 2.898373589998755e-05


In [4]:
#if using IPython

# default 100_000 loops
%timeit my_function()

%timeit -n 1000 my_function() #or specify the number of rounds to run

%timeit -n 100 -r 5 my_function() 
#100 loops of the experiments, and we do this 5 times


27.8 µs ± 1.47 µs per loop (mean ± std. dev. of 7 runs, 10000 loops each)
26.9 µs ± 1.8 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)
32.4 µs ± 2.46 µs per loop (mean ± std. dev. of 5 runs, 100 loops each)


In [5]:
#if using IPython

# default 100_000 loops
%timeit -r 10 my_function()

%timeit -r 10 -n 1000 my_function()



26.6 µs ± 1.26 µs per loop (mean ± std. dev. of 10 runs, 10000 loops each)
26.6 µs ± 1.37 µs per loop (mean ± std. dev. of 10 runs, 1000 loops each)


In [6]:
def f(x):
    return x**2

def g(x):
    return x**4

def h(x):
    return x**8


%timeit -n 100 f(5)

%timeit -n 100 g(5)

%timeit -n 100 h(5)


766 ns ± 33.9 ns per loop (mean ± std. dev. of 7 runs, 100 loops each)
793 ns ± 6.92 ns per loop (mean ± std. dev. of 7 runs, 100 loops each)
814 ns ± 29 ns per loop (mean ± std. dev. of 7 runs, 100 loops each)


# Built-in Functions


- One of the easiest ways to improve Python performance is not to execute any Python code at all! 

- Python provides a large number of built-in functions that perform a wide variety of operations. 

- These built-in functions are written in C, and so are generally very fast. 

- See the Python documentation for a list of the available functions: https://docs.python.org/3/library/functions.html


#### always use the built in function
#### sort
quick sort nlogn 
<br>
bubble sort n^2
#### find the min
at least I need to sweep every number <br>
runtime n

In [17]:
assert 100000 == 100_000 
#the undercore is just for easier reading in python 3.6 and later

In [18]:
import random

def my_min(values):
    min_value = values[0]
    for v in values:
        if v < min_value:
            min_value = v
    return min_value


random_numbers = [random.random() for _ in range(0,100_000)]


#time "my_min()"
%timeit -n 100 my_min(random_numbers)

#IPython already provides the function "min()"
%timeit -n 100 min(random_numbers)


3.74 ms ± 173 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)
2.03 ms ± 196 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


# Function Call Overhead  


**How functions affect a program’s performance?**  

- Function call overhead in Python is relatively high, especially compared with the execution speed of builtin functions. 

- The overhead is mainly due to the dynamic type checking of function arguments that must be performed before and after the function call.  

- One idea is to minimize the number of function calls


In [21]:
%%timeit -n 100 #%%timeit is overhead function

total_sum = 0
def inner(i):
    global total_sum
    total_sum += i
    
# The sum of the first n non-negative integers
# S_{n} = 1 + ... + n 

def outer_1():
    for i in range(10_000 + 1): 
        inner(i)

199 ns ± 31.7 ns per loop (mean ± std. dev. of 7 runs, 100 loops each)


- The "inner" function was called 10000 times. 

- Instead, move the loop inside the "aggregate" function and call it only once!

- different from recursion, because it is calling itself not like the example below calling another function

- do not use global variable

In [22]:
%%timeit -n 100

x = 0
def aggregate(l):
    global x 
    #equivalent to return x for local variable in the function
    for i in l:
        x = x + i

def outer_2():
    aggregate(range(10000))
    

201 ns ± 29.6 ns per loop (mean ± std. dev. of 7 runs, 100 loops each)


## Membership Testing

- Python provides the **in** operator (a membership operator) to check if an element exists in a collection. 

- The **in** operator is very fast at checking if an element exists in a **dict** or a **set**, because both dict and set are implemented using a **hash table**. 

- 26^3


In [26]:
letters = 'abcdefghijklmnopqrstuvwxyz'
letters_list = [x + y + z for x in letters for y in letters for z in letters]

print("first 10 members:", letters_list[:10])
print("last  10 members:", letters_list[-10:])

first 10 members: ['aaa', 'aab', 'aac', 'aad', 'aae', 'aaf', 'aag', 'aah', 'aai', 'aaj']
last  10 members: ['zzq', 'zzr', 'zzs', 'zzt', 'zzu', 'zzv', 'zzw', 'zzx', 'zzy', 'zzz']


In [27]:
print("len_letters_list = %d" % len(letters_list))
print("len_letters ** 3 = %d = %d ** 3" % (len(letters) ** 3, len(letters)))

len_letters_list = 17576
len_letters ** 3 = 17576 = 26 ** 3


In [28]:
"aaa" in letters_list

True

In [31]:
"zzz" in letters_list

True

In [32]:
#Membership of a List
#linear search in a list, thus zzz will take longer than mmm
%timeit ("aaa" in letters_list)
%timeit ("mmm" in letters_list)
%timeit ("zzz" in letters_list)

63.8 ns ± 5.41 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)
149 µs ± 13.1 µs per loop (mean ± std. dev. of 7 runs, 10000 loops each)
310 µs ± 13.4 µs per loop (mean ± std. dev. of 7 runs, 1000 loops each)


### Checking for membership in a list or tuple is not as efficient!

In [34]:
dict([(x,x) for x in [1,2,3]])
# [(1, 1), (2, 2), (3, 3)] change the tuple to the dictionary
#{1: 1, 2: 2, 3: 3}

{1: 1, 2: 2, 3: 3}

In [33]:
#Membership of a Dictionary

# identity mapping: 
letters_dict = dict([(x, x) for x in letters_list])

for k, v in letters_dict.items():
    print(k, ":", v)

aaa : aaa
aab : aab
aac : aac
aad : aad
aae : aae
aaf : aaf
aag : aag
aah : aah
aai : aai
aaj : aaj
aak : aak
aal : aal
aam : aam
aan : aan
aao : aao
aap : aap
aaq : aaq
aar : aar
aas : aas
aat : aat
aau : aau
aav : aav
aaw : aaw
aax : aax
aay : aay
aaz : aaz
aba : aba
abb : abb
abc : abc
abd : abd
abe : abe
abf : abf
abg : abg
abh : abh
abi : abi
abj : abj
abk : abk
abl : abl
abm : abm
abn : abn
abo : abo
abp : abp
abq : abq
abr : abr
abs : abs
abt : abt
abu : abu
abv : abv
abw : abw
abx : abx
aby : aby
abz : abz
aca : aca
acb : acb
acc : acc
acd : acd
ace : ace
acf : acf
acg : acg
ach : ach
aci : aci
acj : acj
ack : ack
acl : acl
acm : acm
acn : acn
aco : aco
acp : acp
acq : acq
acr : acr
acs : acs
act : act
acu : acu
acv : acv
acw : acw
acx : acx
acy : acy
acz : acz
ada : ada
adb : adb
adc : adc
add : add
ade : ade
adf : adf
adg : adg
adh : adh
adi : adi
adj : adj
adk : adk
adl : adl
adm : adm
adn : adn
ado : ado
adp : adp
adq : adq
adr : adr
ads : ads
adt : adt
adu : adu
adv : adv


bgv : bgv
bgw : bgw
bgx : bgx
bgy : bgy
bgz : bgz
bha : bha
bhb : bhb
bhc : bhc
bhd : bhd
bhe : bhe
bhf : bhf
bhg : bhg
bhh : bhh
bhi : bhi
bhj : bhj
bhk : bhk
bhl : bhl
bhm : bhm
bhn : bhn
bho : bho
bhp : bhp
bhq : bhq
bhr : bhr
bhs : bhs
bht : bht
bhu : bhu
bhv : bhv
bhw : bhw
bhx : bhx
bhy : bhy
bhz : bhz
bia : bia
bib : bib
bic : bic
bid : bid
bie : bie
bif : bif
big : big
bih : bih
bii : bii
bij : bij
bik : bik
bil : bil
bim : bim
bin : bin
bio : bio
bip : bip
biq : biq
bir : bir
bis : bis
bit : bit
biu : biu
biv : biv
biw : biw
bix : bix
biy : biy
biz : biz
bja : bja
bjb : bjb
bjc : bjc
bjd : bjd
bje : bje
bjf : bjf
bjg : bjg
bjh : bjh
bji : bji
bjj : bjj
bjk : bjk
bjl : bjl
bjm : bjm
bjn : bjn
bjo : bjo
bjp : bjp
bjq : bjq
bjr : bjr
bjs : bjs
bjt : bjt
bju : bju
bjv : bjv
bjw : bjw
bjx : bjx
bjy : bjy
bjz : bjz
bka : bka
bkb : bkb
bkc : bkc
bkd : bkd
bke : bke
bkf : bkf
bkg : bkg
bkh : bkh
bki : bki
bkj : bkj
bkk : bkk
bkl : bkl
bkm : bkm
bkn : bkn
bko : bko
bkp : bkp
bkq : bkq


crf : crf
crg : crg
crh : crh
cri : cri
crj : crj
crk : crk
crl : crl
crm : crm
crn : crn
cro : cro
crp : crp
crq : crq
crr : crr
crs : crs
crt : crt
cru : cru
crv : crv
crw : crw
crx : crx
cry : cry
crz : crz
csa : csa
csb : csb
csc : csc
csd : csd
cse : cse
csf : csf
csg : csg
csh : csh
csi : csi
csj : csj
csk : csk
csl : csl
csm : csm
csn : csn
cso : cso
csp : csp
csq : csq
csr : csr
css : css
cst : cst
csu : csu
csv : csv
csw : csw
csx : csx
csy : csy
csz : csz
cta : cta
ctb : ctb
ctc : ctc
ctd : ctd
cte : cte
ctf : ctf
ctg : ctg
cth : cth
cti : cti
ctj : ctj
ctk : ctk
ctl : ctl
ctm : ctm
ctn : ctn
cto : cto
ctp : ctp
ctq : ctq
ctr : ctr
cts : cts
ctt : ctt
ctu : ctu
ctv : ctv
ctw : ctw
ctx : ctx
cty : cty
ctz : ctz
cua : cua
cub : cub
cuc : cuc
cud : cud
cue : cue
cuf : cuf
cug : cug
cuh : cuh
cui : cui
cuj : cuj
cuk : cuk
cul : cul
cum : cum
cun : cun
cuo : cuo
cup : cup
cuq : cuq
cur : cur
cus : cus
cut : cut
cuu : cuu
cuv : cuv
cuw : cuw
cux : cux
cuy : cuy
cuz : cuz
cva : cva


eee : eee
eef : eef
eeg : eeg
eeh : eeh
eei : eei
eej : eej
eek : eek
eel : eel
eem : eem
een : een
eeo : eeo
eep : eep
eeq : eeq
eer : eer
ees : ees
eet : eet
eeu : eeu
eev : eev
eew : eew
eex : eex
eey : eey
eez : eez
efa : efa
efb : efb
efc : efc
efd : efd
efe : efe
eff : eff
efg : efg
efh : efh
efi : efi
efj : efj
efk : efk
efl : efl
efm : efm
efn : efn
efo : efo
efp : efp
efq : efq
efr : efr
efs : efs
eft : eft
efu : efu
efv : efv
efw : efw
efx : efx
efy : efy
efz : efz
ega : ega
egb : egb
egc : egc
egd : egd
ege : ege
egf : egf
egg : egg
egh : egh
egi : egi
egj : egj
egk : egk
egl : egl
egm : egm
egn : egn
ego : ego
egp : egp
egq : egq
egr : egr
egs : egs
egt : egt
egu : egu
egv : egv
egw : egw
egx : egx
egy : egy
egz : egz
eha : eha
ehb : ehb
ehc : ehc
ehd : ehd
ehe : ehe
ehf : ehf
ehg : ehg
ehh : ehh
ehi : ehi
ehj : ehj
ehk : ehk
ehl : ehl
ehm : ehm
ehn : ehn
eho : eho
ehp : ehp
ehq : ehq
ehr : ehr
ehs : ehs
eht : eht
ehu : ehu
ehv : ehv
ehw : ehw
ehx : ehx
ehy : ehy
ehz : ehz


fnh : fnh
fni : fni
fnj : fnj
fnk : fnk
fnl : fnl
fnm : fnm
fnn : fnn
fno : fno
fnp : fnp
fnq : fnq
fnr : fnr
fns : fns
fnt : fnt
fnu : fnu
fnv : fnv
fnw : fnw
fnx : fnx
fny : fny
fnz : fnz
foa : foa
fob : fob
foc : foc
fod : fod
foe : foe
fof : fof
fog : fog
foh : foh
foi : foi
foj : foj
fok : fok
fol : fol
fom : fom
fon : fon
foo : foo
fop : fop
foq : foq
for : for
fos : fos
fot : fot
fou : fou
fov : fov
fow : fow
fox : fox
foy : foy
foz : foz
fpa : fpa
fpb : fpb
fpc : fpc
fpd : fpd
fpe : fpe
fpf : fpf
fpg : fpg
fph : fph
fpi : fpi
fpj : fpj
fpk : fpk
fpl : fpl
fpm : fpm
fpn : fpn
fpo : fpo
fpp : fpp
fpq : fpq
fpr : fpr
fps : fps
fpt : fpt
fpu : fpu
fpv : fpv
fpw : fpw
fpx : fpx
fpy : fpy
fpz : fpz
fqa : fqa
fqb : fqb
fqc : fqc
fqd : fqd
fqe : fqe
fqf : fqf
fqg : fqg
fqh : fqh
fqi : fqi
fqj : fqj
fqk : fqk
fql : fql
fqm : fqm
fqn : fqn
fqo : fqo
fqp : fqp
fqq : fqq
fqr : fqr
fqs : fqs
fqt : fqt
fqu : fqu
fqv : fqv
fqw : fqw
fqx : fqx
fqy : fqy
fqz : fqz
fra : fra
frb : frb
frc : frc


...

ryi : ryi
ryj : ryj
ryk : ryk
ryl : ryl
rym : rym
ryn : ryn
ryo : ryo
ryp : ryp
ryq : ryq
ryr : ryr
rys : rys
ryt : ryt
ryu : ryu
ryv : ryv
ryw : ryw
ryx : ryx
ryy : ryy
ryz : ryz
rza : rza
rzb : rzb
rzc : rzc
rzd : rzd
rze : rze
rzf : rzf
rzg : rzg
rzh : rzh
rzi : rzi
rzj : rzj
rzk : rzk
rzl : rzl
rzm : rzm
rzn : rzn
rzo : rzo
rzp : rzp
rzq : rzq
rzr : rzr
rzs : rzs
rzt : rzt
rzu : rzu
rzv : rzv
rzw : rzw
rzx : rzx
rzy : rzy
rzz : rzz
saa : saa
sab : sab
sac : sac
sad : sad
sae : sae
saf : saf
sag : sag
sah : sah
sai : sai
saj : saj
sak : sak
sal : sal
sam : sam
san : san
sao : sao
sap : sap
saq : saq
sar : sar
sas : sas
sat : sat
sau : sau
sav : sav
saw : saw
sax : sax
say : say
saz : saz
sba : sba
sbb : sbb
sbc : sbc
sbd : sbd
sbe : sbe
sbf : sbf
sbg : sbg
sbh : sbh
sbi : sbi
sbj : sbj
sbk : sbk
sbl : sbl
sbm : sbm
sbn : sbn
sbo : sbo
sbp : sbp
sbq : sbq
sbr : sbr
sbs : sbs
sbt : sbt
sbu : sbu
sbv : sbv
sbw : sbw
sbx : sbx
sby : sby
sbz : sbz
sca : sca
scb : scb
scc : scc
scd : scd


tht : tht
thu : thu
thv : thv
thw : thw
thx : thx
thy : thy
thz : thz
tia : tia
tib : tib
tic : tic
tid : tid
tie : tie
tif : tif
tig : tig
tih : tih
tii : tii
tij : tij
tik : tik
til : til
tim : tim
tin : tin
tio : tio
tip : tip
tiq : tiq
tir : tir
tis : tis
tit : tit
tiu : tiu
tiv : tiv
tiw : tiw
tix : tix
tiy : tiy
tiz : tiz
tja : tja
tjb : tjb
tjc : tjc
tjd : tjd
tje : tje
tjf : tjf
tjg : tjg
tjh : tjh
tji : tji
tjj : tjj
tjk : tjk
tjl : tjl
tjm : tjm
tjn : tjn
tjo : tjo
tjp : tjp
tjq : tjq
tjr : tjr
tjs : tjs
tjt : tjt
tju : tju
tjv : tjv
tjw : tjw
tjx : tjx
tjy : tjy
tjz : tjz
tka : tka
tkb : tkb
tkc : tkc
tkd : tkd
tke : tke
tkf : tkf
tkg : tkg
tkh : tkh
tki : tki
tkj : tkj
tkk : tkk
tkl : tkl
tkm : tkm
tkn : tkn
tko : tko
tkp : tkp
tkq : tkq
tkr : tkr
tks : tks
tkt : tkt
tku : tku
tkv : tkv
tkw : tkw
tkx : tkx
tky : tky
tkz : tkz
tla : tla
tlb : tlb
tlc : tlc
tld : tld
tle : tle
tlf : tlf
tlg : tlg
tlh : tlh
tli : tli
tlj : tlj
tlk : tlk
tll : tll
tlm : tlm
tln : tln
tlo : tlo


uzm : uzm
uzn : uzn
uzo : uzo
uzp : uzp
uzq : uzq
uzr : uzr
uzs : uzs
uzt : uzt
uzu : uzu
uzv : uzv
uzw : uzw
uzx : uzx
uzy : uzy
uzz : uzz
vaa : vaa
vab : vab
vac : vac
vad : vad
vae : vae
vaf : vaf
vag : vag
vah : vah
vai : vai
vaj : vaj
vak : vak
val : val
vam : vam
van : van
vao : vao
vap : vap
vaq : vaq
var : var
vas : vas
vat : vat
vau : vau
vav : vav
vaw : vaw
vax : vax
vay : vay
vaz : vaz
vba : vba
vbb : vbb
vbc : vbc
vbd : vbd
vbe : vbe
vbf : vbf
vbg : vbg
vbh : vbh
vbi : vbi
vbj : vbj
vbk : vbk
vbl : vbl
vbm : vbm
vbn : vbn
vbo : vbo
vbp : vbp
vbq : vbq
vbr : vbr
vbs : vbs
vbt : vbt
vbu : vbu
vbv : vbv
vbw : vbw
vbx : vbx
vby : vby
vbz : vbz
vca : vca
vcb : vcb
vcc : vcc
vcd : vcd
vce : vce
vcf : vcf
vcg : vcg
vch : vch
vci : vci
vcj : vcj
vck : vck
vcl : vcl
vcm : vcm
vcn : vcn
vco : vco
vcp : vcp
vcq : vcq
vcr : vcr
vcs : vcs
vct : vct
vcu : vcu
vcv : vcv
vcw : vcw
vcx : vcx
vcy : vcy
vcz : vcz
vda : vda
vdb : vdb
vdc : vdc
vdd : vdd
vde : vde
vdf : vdf
vdg : vdg
vdh : vdh


wss : wss
wst : wst
wsu : wsu
wsv : wsv
wsw : wsw
wsx : wsx
wsy : wsy
wsz : wsz
wta : wta
wtb : wtb
wtc : wtc
wtd : wtd
wte : wte
wtf : wtf
wtg : wtg
wth : wth
wti : wti
wtj : wtj
wtk : wtk
wtl : wtl
wtm : wtm
wtn : wtn
wto : wto
wtp : wtp
wtq : wtq
wtr : wtr
wts : wts
wtt : wtt
wtu : wtu
wtv : wtv
wtw : wtw
wtx : wtx
wty : wty
wtz : wtz
wua : wua
wub : wub
wuc : wuc
wud : wud
wue : wue
wuf : wuf
wug : wug
wuh : wuh
wui : wui
wuj : wuj
wuk : wuk
wul : wul
wum : wum
wun : wun
wuo : wuo
wup : wup
wuq : wuq
wur : wur
wus : wus
wut : wut
wuu : wuu
wuv : wuv
wuw : wuw
wux : wux
wuy : wuy
wuz : wuz
wva : wva
wvb : wvb
wvc : wvc
wvd : wvd
wve : wve
wvf : wvf
wvg : wvg
wvh : wvh
wvi : wvi
wvj : wvj
wvk : wvk
wvl : wvl
wvm : wvm
wvn : wvn
wvo : wvo
wvp : wvp
wvq : wvq
wvr : wvr
wvs : wvs
wvt : wvt
wvu : wvu
wvv : wvv
wvw : wvw
wvx : wvx
wvy : wvy
wvz : wvz
wwa : wwa
wwb : wwb
wwc : wwc
wwd : wwd
wwe : wwe
wwf : wwf
wwg : wwg
wwh : wwh
wwi : wwi
wwj : wwj
wwk : wwk
wwl : wwl
wwm : wwm
wwn : wwn


ymc : ymc
ymd : ymd
yme : yme
ymf : ymf
ymg : ymg
ymh : ymh
ymi : ymi
ymj : ymj
ymk : ymk
yml : yml
ymm : ymm
ymn : ymn
ymo : ymo
ymp : ymp
ymq : ymq
ymr : ymr
yms : yms
ymt : ymt
ymu : ymu
ymv : ymv
ymw : ymw
ymx : ymx
ymy : ymy
ymz : ymz
yna : yna
ynb : ynb
ync : ync
ynd : ynd
yne : yne
ynf : ynf
yng : yng
ynh : ynh
yni : yni
ynj : ynj
ynk : ynk
ynl : ynl
ynm : ynm
ynn : ynn
yno : yno
ynp : ynp
ynq : ynq
ynr : ynr
yns : yns
ynt : ynt
ynu : ynu
ynv : ynv
ynw : ynw
ynx : ynx
yny : yny
ynz : ynz
yoa : yoa
yob : yob
yoc : yoc
yod : yod
yoe : yoe
yof : yof
yog : yog
yoh : yoh
yoi : yoi
yoj : yoj
yok : yok
yol : yol
yom : yom
yon : yon
yoo : yoo
yop : yop
yoq : yoq
yor : yor
yos : yos
yot : yot
you : you
yov : yov
yow : yow
yox : yox
yoy : yoy
yoz : yoz
ypa : ypa
ypb : ypb
ypc : ypc
ypd : ypd
ype : ype
ypf : ypf
ypg : ypg
yph : yph
ypi : ypi
ypj : ypj
ypk : ypk
ypl : ypl
ypm : ypm
ypn : ypn
ypo : ypo
ypp : ypp
ypq : ypq
ypr : ypr
yps : yps
ypt : ypt
ypu : ypu
ypv : ypv
ypw : ypw
ypx : ypx


In [35]:
%timeit ("aaa" in letters_dict)
%timeit ("mmm" in letters_dict)
%timeit ("zzz" in letters_dict)
#change the list to a dictionary will increase your search time drastically
#when the length of the list increases

62.5 ns ± 4.42 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)
66.5 ns ± 3.45 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)
66.7 ns ± 4.74 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)


### You could also convert a list into a set and check for a membership

---

In [ ]:
#if your job is to repeatly to search for element, 
#you might want to pre-proces the list once before hand

In [36]:
letters_set = set(letters_list)

%timeit ("aaa" in letters_set)
%timeit ("mmm" in letters_set)a
%timeit ("zzz" in letters_set)

57.6 ns ± 1.92 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)
58.6 ns ± 1.6 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)
60.4 ns ± 1.28 ns per loop (mean ± std. dev. of 7 runs, 10000000 loops each)


## String Concatenation

In [37]:
def make_string(string_list):
    my_string = ''
    for character in string_list:
        my_string += character
    return my_string

str_list = [character for character in 'abcdefghijklmnopqrstuvwxyz']
print(str_list)

['a', 'b', 'c', 'd', 'e', 'f', 'g', 'h', 'i', 'j', 'k', 'l', 'm', 'n', 'o', 'p', 'q', 'r', 's', 't', 'u', 'v', 'w', 'x', 'y', 'z']


In [38]:
%timeit make_string(str_list)

2.22 µs ± 143 ns per loop (mean ± std. dev. of 7 runs, 100000 loops each)


In [39]:
%timeit "".join(str_list) #shorter time than self-defined function

349 ns ± 11.4 ns per loop (mean ± std. dev. of 7 runs, 1000000 loops each)


1 uS = 1000 nS

# Decorator Caching

## Function Decorator



---

- The symbol **@** is Python decorator syntax. 


- Python decorators are callable Python object that is used to modify a function, method or class definition.   


- Python decorators are normally used for tracking, locking, or logging  


- The wise use of decorators can improve the performance of codes.  


- Decorate a Python function so that it remembers the results needed later  

---

In [50]:
def decorating_a_function(func):
    def function_wrapper(x):
        print("Now \"" + func.__name__ + "\" becomes decorated.")
        print("The attribute:")
        func(x)
        print("is surrounded by all these text!")
    return function_wrapper

def foo(x):
    print(x)

In [51]:
# run the function
foo("test")

# separator
print("-" * 50)

# get the function name
print("function_name:", foo.__name__)

test
--------------------------------------------------
function_name: foo


In [52]:
foo = decorating_a_function(foo)
print("-" * 50)

# run the function
foo("test")

# separator
print("-" * 50)

# get the function name
print(foo.__name__)

--------------------------------------------------
Now "foo" becomes decorated.
The attribute:
test
is surrounded by all these text!
--------------------------------------------------
function_wrapper


In [53]:
def decorating_a_function(func):
    def function_wrapper(x):
        print("Now the function called \"" + func.__name__ + "\" becomes decorated.")
        print("The attribute of the function:")
        func(x)
        print("is surrounded by all this text!")
    return function_wrapper

@decorating_a_function
def foo(x):
    print(x)

In [54]:
# Test 1:
foo("test")

Now the function called "foo" becomes decorated.
The attribute of the function:
test
is surrounded by all this text!


In [55]:
# Test 2:
print(foo.__name__)

function_wrapper


## Imported functions can also be decorated

In [ ]:
from math import sin, cos, pi

def our_decorator(func):
    def function_wrapper(x):
        print("The result of %s(%0.4f) is: %0.4f" % (func.__name__, x, func(x)))
    return function_wrapper

# in this case is not possible to use @
sin = our_decorator(sin)
cos = our_decorator(cos)

for f in [sin, cos]: f(pi/2)

for f in [sin, cos]: f(pi)
    


## Using wraps from module functools

- a module with higher-order functions and operations on callable objects

In [56]:
from functools import wraps

def greeting(func):
    @wraps(func)
    def function_wrapper(x):
        """function_wrapper of greeting"""
        print("Hello, this function " + func.__name__ + " at value " + str(x) + " returns:", func(x))
    
    return function_wrapper

@greeting
def simple_f(x):
    """this is a docstring of some simple function"""
    return (x + 500)

In [57]:
#call simple_f
simple_f(10)

Hello, this function simple_f at value 10 returns: 510


In [58]:
print("function name: " + simple_f.__name__)
print("docstring: " + simple_f.__doc__)
print("module name: " + simple_f.__module__)

function name: simple_f
docstring: this is a docstring of some simple function
module name: __main__


# Using Decorators for Caching

In [4]:
import time

# Consider Fibonacci numbers: 
# defined as f_n = f_{n - 1} + f_{n - 2} for n >=2 
# where f_0 = 0 and f_1 = 1
# https://en.wikipedia.org/wiki/Fibonacci_number
    

# a simple recursion: 
def fib(i):
    if i <= 1: return i
    return fib(i - 1) + fib(i - 2)

#0, 1, 1, 2, 3, 5, 8, 13, 21, 34, ...

t = time.process_time() 
fib_result = fib(30)
elapsed_time = time.process_time() - t
print("fibonacci time: %0.10f; fib_result: %d" % (elapsed_time, fib_result))

fibonacci time: 0.8174400000; fib_result: 832040


# Memoization

In [5]:
# The idea is a memoization: 
# introduce a map (dictionary) "memo"
# in which to save intermediate steps
# of calculations

#store the intermediate steps

def fib_memo(i, memo=dict()):
    if i <= 1: return i
    if i in memo: return memo[i]

    memo[i] = fib_memo(i - 1, memo) + fib_memo(i - 2, memo)
    return memo[i]

t = time.process_time() 
fib_m = fib_memo(30)
elapsed_time_memo = time.process_time() - t
print("fibonacci time: %0.10f; fib_result: %d" % (elapsed_time_memo, fib_m))

fibonacci time: 0.0001540000; fib_result: 832040


In [6]:
# We can create a decorator that saves:
# each intermediate value in memory 
# rather than calculating it every time.

from functools import wraps
import time

def cache(f):
    memo = {}
    @wraps(f)
    def function_wrapper(*arg):
        if arg not in memo: memo[arg] = f(*arg)
        return memo[arg] 
    return function_wrapper
#by decorating, we introduce the dictionary, if cal=> cal, else return f(*arg)
@cache
def fib_cache(i):
    if i < 2: return i
    return fib(i - 1) + fib(i - 2)


t = time.process_time() 
fib_c = fib_cache(30)
elapsed_time_c = time.process_time() - t
print("fibonacci time: %0.10f; result: %d" % (elapsed_time_c, fib_c))

fibonacci time: 0.8570560000; result: 832040


# Optimizing Loops

In [69]:
import random

lowerlist = ['abcdefghijklmnopqrstuvwxyz'[:random.randint(0, 26)] for x in range(10_00)]
upperlist = []

# get firs 20 elements
lowerlist[ : 20]

['abcdefghijklmnopqrstuvwx',
 'abcdefghijklmn',
 'abcdefghijklm',
 'abcdefghijklmnopqrstuv',
 'abcdefghijklm',
 'abcdefghijkl',
 'abcdefghi',
 'abcdefghijk',
 'abcdefghijklmno',
 'ab',
 'a',
 'abc',
 'a',
 'abcdefghi',
 'abcdefghijklmnopqrstuvwxyz',
 'abcdefghijklmno',
 'abcdef',
 'abcdefghijklmnopqrstuv',
 'abcde',
 'abcdefghijklm']

### Task: From the lowerlist build the upperlist

In [70]:
%%timeit -n 100

def to_upper_1():
    for word in lowerlist:
        upperlist.append(str.upper(word))
    return upperlist

to_upper_1()

298 µs ± 72.9 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


- The loop calls two methods: "upperlist.append" and "str.upper" every time. 

- Python must support dynamic attributes as well as multiple namespaces. 


In [71]:
%%timeit -n 100

f_upper = str.upper
f_append = upperlist.append

def to_upper_2():
    for word in lowerlist:
        f_append(f_upper(word))

to_upper_2()

222 µs ± 43.2 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


### Avoid the loop

In [72]:
# A "map" is often called "apply-to-all" when considered in functional form;
# e.g. a map applied on all elements of a list

simple_mapping = map(lambda x : x + 100, [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10])

list(simple_mapping)

[100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110]

In [73]:
# Apply the method "upper" on strings

print(lowerlist[0], str.upper(lowerlist[0]))

abcdefghijklmnopqrstuvwx ABCDEFGHIJKLMNOPQRSTUVWX


In [74]:
%%timeit -n 100

# avoiding the loop by using "map"
upper = str.upper

upperlist = list(map(upper, lowerlist))

147 µs ± 32.6 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [75]:
%%timeit -n 100

# avoiding the loop by using "list comprehension"
f_upper = str.upper 
upperlist = [f_upper(word) for word in lowerlist]

138 µs ± 19.9 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [63]:
# add two random vectors; given as lists

import random 

random_numbers1 = [random.random() for _ in range(0,100000)]
random_numbers2 = [random.random() for _ in range(0,100000)]

%timeit res1 = list(map(lambda x, y: x + y, random_numbers1, random_numbers2))

# However map is calling our function as "adding two vectors" not as "cross product" 

13.8 ms ± 1.17 ms per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [64]:
len(list(map(lambda x, y: x + y, random_numbers1, random_numbers2)))

100000

## Intrinsic Opertors

- Another performance improvement is to use intrinsic operators (+, -, *, etc.) instead of a user defined function.  


- The operator module exports a set of efficient functions corresponding to the intrinsic operators of Python.   


- operator.add(x, y) is equivalent to the expression x + y.   


- **import operator**  

https://docs.python.org/3.4/library/operator.html

In [76]:
import operator

%timeit res2 = list(map(operator.add, random_numbers1, random_numbers2))

7.85 ms ± 847 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


### using maps

- In Python 3.5, **the map function returns an iterator that does not evaluate the arguments until it needs to**. 

-  By converting the iterator to a list, we are forcing map to compute every value.


In [77]:
#Instead here we use the operator "add" directly without "map":

%timeit res3 = operator.add(random_numbers1, random_numbers2)

1.74 ms ± 214 µs per loop (mean ± std. dev. of 7 runs, 100 loops each)


In [78]:
res4 = operator.add(random_numbers1, random_numbers2)

for e in res4: 
    print(e)

0.7676767657897398
0.4140179594787087
0.5965561304343673
0.38073213603666245
0.6511481342737797
0.3572699438605983
0.30180306787403943
0.11939546022031211
0.9369917686849772
0.9412622915615269
0.640171123817851
0.4301503946891483
0.15099848223817314
0.1705888991871526
0.6138457126071948
0.6491084786876639
0.5100878571684967
0.32449789251630334
0.900784122173595
0.01913227058917466
0.5795859811799973
0.3152912617721667
0.8010858556824478
0.5079525542970394
0.2134507425372686
0.07050585999390224
0.08707563712104915
0.8657343331994763
0.9143659068152029
0.8478046690536178
0.5139995352650493
0.7436877737908235
0.7895338065933003
0.58916221405539
0.42907260372424827
0.7022283020841842
0.2353989953479313
0.7865629336494996
0.7027729064996243
0.7547976557916922
0.2871910081466267
0.19858900379039945
0.39049941872379856
0.2827680146590771
0.17609060346150207
0.7200127147032737
0.43169209487525073
0.5678276910557435
0.09408265848838404
0.2967529358434198
0.06948494673116423
0.9236721723089846
0

0.40624400576339004
0.43349032895799666
0.5047309994996637
0.8545820389780905
0.991146178761995
0.2151846796420136
0.6352294377339402
0.8388096704031862
0.17587965879740952
0.1928876781750296
0.06239787837531052
0.5162790016240785
0.9183955281905188
0.7720593559229936
0.5435403812051481
0.37069889123192057
0.13269859833426334
0.9581190671596734
0.7771668186212851
0.21907044444140544
0.8399750824040985
0.09082733039751867
0.8287528162006446
0.8483381187946996
0.5006107463954846
0.4191228171818593
0.5625613835930797
0.9471922894547136
0.5011995620030346
0.3066084808234514
0.1074441123749903
0.6074403957659844
0.22801702556049463
0.8139092297849901
0.1152504719528693
0.35203854199540263
0.7509918478200751
0.09529455150006194
0.9820778364813746
0.7886877562262745
0.17179296148754308
0.7613530453471465
0.74486819951101
0.17449009112737546
0.9960509213704641
0.450917184035159
0.1837392370243559
0.11725021909563471
0.26183608204203135
0.6761619612895836
0.17176495818106752
0.5293974030185824


0.19954945412841918
0.3626157303637537
0.9231174784136779
0.033696627284349745
0.5490890190672776
0.12135392775226828
0.25834265306713566
0.7757090594569944
0.11575242226910976
0.5507063003812593
0.594918371335345
0.33407978881276845
0.1592251262104476
0.17474646551721895
0.6128656223381789
0.5717519617970618
0.9945008826814407
0.6179120707909894
0.3582776905586659
0.9105895606781022
0.5683380016569427
0.4648991517676341
0.5730233283628109
0.6619829307796097
0.7126634390070937
0.5441264476592734
0.872715693573158
0.7967013706242012
0.5896708566146411
0.0033171351812533167
0.4426446464735315
0.21469256069529552
0.5721023509393617
0.9385435615441621
0.6766807596906559
0.19416228879900344
0.6693086466475076
0.3626870681113421
0.3042203310702165
0.1847955260234081
0.47504608506984625
0.23443038121149662
0.06633082782452326
0.7891278561312823
0.1767864814929263
0.05827992336882448
0.1681736841156123
0.9891755507629363
0.399627051787376
0.8453102522117442
0.8949247259632884
0.859098270046193

0.13756429156015415
0.20649422195527567
0.976654470758837
0.09669214778632229
0.7029704137064173
0.7497530657864502
0.7669386335919982
0.18628047308416718
0.533742946901008
0.9226095910816015
0.7264331289331666
0.23618823048606385
0.8536593169696591
0.6424407518067874
0.31205725322969646
0.7415489234322689
0.5597087954659307
0.7397750378530938
0.21576484946741425
0.7259885327898803
0.9515960856525042
0.059348705124240175
0.5797492272486527
0.5785394082067687
0.6505796997672991
0.5124441795547374
0.3300634947064385
0.36179435790292014
0.27530963715336465
0.7303837642410956
0.5171937751719907
0.9325547135747623
0.6494382272719177
0.5735183100371646
0.03219393601824494
0.020368308602615515
0.7231724068659049
0.6561613135426178
0.5561956590310603
0.5883163282144807
0.970105949950726
0.2008804983011837
0.5822672097921194
0.1669177185305858
0.7809391824635287
0.6800516092205964
0.8502094223079395
0.6231752009080188
0.5042554324673392
0.03231395866328113
0.6167070502694622
0.07052803367867655

0.5392428299561579
0.00451312588213193
0.42972812348971534
0.03262428253470773
0.8806840511642757
0.5216870913715449
0.5470020429389505
0.35333199273997795
0.6190312356230852
0.792403466829294
0.027401663269561394
0.31867066392040944
0.3090372770295522
0.8983885990940064
0.69203061082048
0.6882833982762769
0.5253756096734146
0.24412829046480677
0.5712598982113315
0.6872026147523161
0.3587908835574827
0.11757722107679303
0.442166859473449
0.36351600825688635
0.6196876778674696
0.5582557717623442
0.9055065965293045
0.8848181389175236
0.8914742432474951
0.5372441821700129
0.976879742500917
0.12852361420229486
0.5482307977291555
0.724976941220385
0.9332755374291647
0.5861319604195752
0.2740968013482069
0.5910924412303017
0.2086852614073874
0.03401555407145751
0.2991586593228448
0.008738825654136195
0.6438970018179504
0.06832485063213056
0.011318756302337918
0.5522102341174077
0.8280062495795438
0.23635900939177035
0.5841194024810165
0.5674159468342079
0.8078831329926665
0.5260474966502001


...

0.6019207732916083
0.5960882559828726
0.8064537788507257
0.9441898294033007
0.3188159779256159
0.7832365024604931
0.08689239574250074
0.5395208348560991
0.5558828713756827
0.6443573272359054
0.6223492674565005
0.27780697290136735
0.8854488949726897
0.005056977764934634
0.6232424310254556
0.9616270841953889
0.34579549632703843
0.13011188928754092
0.7866568935413972
0.8120712637476457
0.857601053088836
0.29707647648975055
0.06876713237499466
0.5803484541933958
0.3630265062622231
0.15175036859712987
0.6456977202939539
0.567037346097016
0.8723014222387075
0.9694259706881083
0.017021621149651667
0.4073837856395809
0.6125341029097732
0.6909059796555072
0.9735130044562027
0.41761219496560764
0.8933552185741275
0.17938155386894805
0.07502419267900451
0.029231505097338628
0.915606037425837
0.6531837035202112
0.28859425010073725
0.010330655126106536
0.392410469301248
0.01098481726144862
0.9386881000871015
0.8579167794586968
0.08257166200896238
0.6628451479199124
0.36943812446942237
0.80005586067

0.45807248860004146
0.555319925234045
0.9124823255780959
0.9099181780043845
0.40295787711790354
0.1934271605677066
0.32930174986816296
0.0034721195293381246
0.5401494755026828
0.35691552028288875
0.1716370716804605
0.29480344883518583
0.4093316500941351
0.5193952447889422
0.8015435975745447
0.8928398891282878
0.20536836253711355
0.4075914216065425
0.19404761628671496
0.9522880701253482
0.3848234576412717
0.12958976046618798
0.1381289617499032
0.09964711493021006
0.1002358984471019
0.03068584755606074
0.04009790844103167
0.9684077706250447
0.5605719200180778
0.7565566331536744
0.6650715499913357
0.08578545552325023
0.7446919401881067
0.9703847312812933
0.9740645282897323
0.49108196567747
0.06452048136369015
0.7669867528302279
0.5586437640846518
0.904401999809821
0.8005773107012816
0.1528073327600804
0.13782189385836452
0.7023801163208241
0.5482656863337013
0.06730257405854745
0.7402965092942024
0.8758724132647755
0.6449874669305342
0.3645207670890619
0.751093686394275
0.3792788571515151

0.3765823128001732
0.5448567773921045
0.3514361544843537
0.8340628611904455
0.2639523930938402
0.8431830999499093
0.8209930668168529
0.806732505229042
0.23520816147227652
0.7922875488786318
0.6761860376826493
0.7105510163673299
0.16395417419996816
0.9523342205852097
0.9634123001732915
0.7998855550773355
0.585746453895258
0.2586377484922736
0.6756817937887923
0.08522160353377584
0.32740398521061265
0.598009294199488
0.6385564237323408
0.613281738828968
0.11909612633322908
0.3043047415043324
0.012567572651836945
0.3866027561195826
0.04247844832847725
0.8698567906080018
0.14170563171958384
0.846588612856325
0.14801331746376034
0.17749164669801498
0.21262000611574172
0.7093595679068377
0.8744239641848561
0.26368507845105893
0.38825256373126205
0.48169838289503986
0.34555516594878144
0.7736805843188312
0.769590445995758
0.90897512665505
0.8773800379380641
0.49213388024252147
0.5829539236736047
0.09424781797355264
0.018509386871568556
0.9072395071139022
0.3236247422685795
0.06466347785819793

0.06730831902002021
0.89892899946467
0.19690317498025078
0.580874375209723
0.6268040238771818
0.3376211042771057
0.001864678290555477
0.2618828342521461
0.583626843291647
0.6834166330901412
0.5550471239019498
0.5503141824021368
0.6225957865077272
0.28060843406032265
0.18858794829617598
0.41182630456676117
0.7916195400222428
0.6057218021077831
0.8829316095455291
0.28536978381213285
0.890282789999498
0.8634394614038523
0.08475058311152128
0.7576033294650913
0.11361266126009228
0.8423061286351499
0.2141704623616626
0.6436379641204428
0.14168439172379932
0.08762927481104421
0.052997039800260826
0.26798940562237816
0.003688063273336928
0.2311754514555372
0.9393245916521367
0.08828198991736702
0.3884175253489033
0.5482064830532264
0.663486339354324
0.35587840483179356
0.11766351666004249
0.054285820898759996
0.9346918846863627
0.41950998085434976
0.13490546236102563
0.7973638191682564
0.5509158336413249
0.4991637396033909
0.7531593998368292
0.9795018034189772
0.04731934668976523
0.5802847597

0.07369239693554852
0.3357962421012066
0.23657767313309397
0.7066689471336717
0.8175060858579553
0.6007930468250031
0.9237342416666027
0.9386080180576324
0.21634698436569455
0.6775643289405755
0.9909679371898888
0.20065874554218244
0.5907231957911641
0.4598499845494115
0.472789300167029
0.2617893111236861
0.2776235988704455
0.48902788573212363
0.7704851800650064
0.6600469935543699
0.7964578018390984
0.8689281951606825
0.31072380638819097
0.2665953463401821
0.17004794467919293
0.5421504381283224
0.7472198388118667
0.5352331181826205
0.5381611956173267
0.6458539497140292
0.4752767688670534
0.9812678175487785
0.9678384413393887
0.767043768772854
0.6712555765503881
0.5274046007463553
0.20292002462345637
0.8348694972557955
0.39398458811637826
0.8880889655157141
0.9760666925746374
0.6952315652160705
0.2943277327955883
0.9531957497820254
0.5466381399321768
0.9756574378668094
0.42084139752721517
0.8283779347124703
0.7219530459255946
0.39860430548553283
0.28631255623671503
0.15801099265883323
0

In [79]:
_iter = map(operator.add, range(10), range(10))
list(_iter)

[0, 2, 4, 6, 8, 10, 12, 14, 16, 18]